In [2]:
import numpy as np
import pandas as pd
import h5py
import bisect

In [3]:
# detector parameters from Patrick's paper

L = 6000. # microns
sigma = 70 # degrees
#sigma = 90.
theta_C = 0. 
alpha = 90. - sigma + theta_C # degrees
#alpha = 0.
delta = 55 # microns
x_pixels = 256
y_pixels = 256
x_PC = 10. 
y_PC = 20. 
#x_PC = 0.
#y_PC = 0.
bin_size = 1

In [3]:
# x_d = np.linspace(-x_pixels/2., x_pixels/2., num=x_pixels/bin_size) # pixels 
# y_d = np.linspace(-y_pixels/2., y_pixels/2., num=y_pixels/bin_size ) # pixels

# Xdet_grid, Ydet_grid = np.meshgrid(x_d, y_d)

# t_x = (y_PC - Ydet_grid)*delta*np.cos(np.radians(alpha)) + L*np.sin(np.radians(alpha))
# t_y = (x_PC - Xdet_grid)*delta
# t_z = (y_PC - Ydet_grid)*delta*np.sin(np.radians(alpha)) + L*np.cos(np.radians(alpha))

# q = np.sqrt(t_x*t_x + t_y*t_y + t_z*t_z)
# tx_norm = t_x/q
# ty_norm = t_y/q

# file_name = 'data/BSE70tiltcont.h5'
# h5data = h5py.File(file_name,'r+')   


# dirx = h5data['BSE']['block0_values'][1]
# diry = h5data['BSE']['block0_values'][2]
# dirz = h5data['BSE']['block0_values'][3]

# energy = h5data['BSE']['block0_values'][0]


# counts = np.zeros(tx_norm.shape)
# onDetector = (min(tx_norm[:,1]) <= dirx) & (dirx <= max(tx_norm[:,1])) & ((min(ty_norm[:,1]) <= diry) & (diry <= max(ty_norm[:,1])))

# for direction in dirXY[0]:
#     if( min(tx_norm.any())<= direction[0] <=max(tx_norm.any())):

    

In [4]:
import quaternion
import h5py 
from math import cos, sqrt, sin

import plotly.graph_objs as go
from plotly import tools

def projOnDetector(xyz_, alpha_, xy_PC_, L_):
    '''
    calculate the projection on the detector of a given escape direction

    xyz = array of escape direction unit vectors in sampe frame
    alpha = angle in degrees that brings the detector frame coincidental with the sample frame
            by a CW rotation around x-axis

    returns list of x,y projection on the detector
    '''
    # let t be the translation vector from detector frame origin to the sample frame origin
    t = np.array([xy_PC_[0], xy_PC_[1], L_])
    
    # let q_DS be the passive rotation (P=-1) that brings in coincidence the detector frame with the sample frame
    # q_DS = * (z, 90).conj() * (x, alpha).conj()
    c_hAlpha = cos(np.radians(alpha_)/2.)
    s_hAlpha = (1. - c_hAlpha**2)**0.5
    q_DS = np.quaternion(sqrt(2.)/2., 0., 0., sqrt(2.)/2.).conj() * np.quaternion(c_hAlpha, s_hAlpha, 0., 0.).conj()
    
    # escape direction in detector frame is the inverse rotation of the above, ie its conjugate 
    dir_detF = [(quaternion.rotate_vectors(q_DS.conj(), one_dir) )   for one_dir in xyz_]
    
    # the xy_det 
    return [np.array([ t[0]- (one_dir[0]*t[2]/one_dir[2]), 
                       t[1]- (one_dir[1]*t[2]/one_dir[2]) ] )   for one_dir in dir_detF]



def projOnSample(xy_, alpha_, xy_PC_, L_):
    '''
    the xyz escape direction in the sample frame for a detector pixel
    '''
    
    # let t be the translation vector from detector frame origin to the sample frame origin
    t = np.array([xy_PC_[0], xy_PC_[1], L_])
    
    # let q_DS be the passive rotation (P=-1) that brings in coincidence the detector frame with the sample frame
    # q_DS = * (z, 90).conj()*(x, alpha).conj()
    c_hAlpha = cos(np.radians(alpha_)/2.)
    s_hAlpha = sin(np.radians(alpha_)/2.)
    q_DS =  np.quaternion(sqrt(2.)/2., 0., 0., sqrt(2.)/2.).conj() * (np.quaternion(c_hAlpha, s_hAlpha, 0., 0.).conj())

    xyz_ = [np.array([position[0]-t[0], position[1]-t[1], -t[2] ]) for position in xy_ ]
    
    # detector pixel is the escape direction in sample frame:
    pixel_sampleF = [(quaternion.rotate_vectors(q_DS, pixel ) )   for pixel in xyz_]
    return pixel_sampleF



def projOnSample_patrick(xy_, alpha_, xy_PC_, L_):
    '''
    the xyz escape direction in the sample frame for a detector pixel
    '''
    #alpha = 180. + alpha_
    alpha = alpha_
    cosAlpha = cos(np.radians(alpha))
    sinAlpha = sin(np.radians(alpha))
    position = [np.array([ L_*sinAlpha + ((xy_PC_[1] - xy[1])*cosAlpha),
                        xy_PC_[0]- xy[0],
                     L_*cosAlpha - ((xy_PC_[1] - xy[1])*sinAlpha) ]) for xy in xy_] 
    q_PE = np.quaternion(0., 0., 1., 0.)
    
    return [quaternion.rotate_vectors(q_PE.conj(), position_i) for position_i in position]

# def projOnSample_patrick(xy_, alpha_, xy_PC_, L_):
#     '''
#     the xyz escape direction in the sample frame for a detector pixel
#     '''
#     alpha =  180.+alpha_
#     #alpha = alpha_
    
#     # let t be the translation vector from detector frame origin to the sample frame origin
#     t = np.array([xy_PC_[0], xy_PC_[1], L_])
    
#     # let q_DS be the passive rotation (P=-1) that brings in coincidence the detector frame with the sample frame
#     # q_DS = * (z, 270).conj()*(x, alpha).conj()
#     c_hAlpha = cos(np.radians(alpha)/2.)
#     s_hAlpha = sin(np.radians(alpha)/2.)
#     q_DS =  np.quaternion(0., 0., 1., 0.).conj()*  np.quaternion(sqrt(2.)/2., 0., 0., sqrt(2.)/2.).conj() * np.quaternion(c_hAlpha, s_hAlpha, 0., 0.).conj()
#     xyz_ = [np.array([position[0]-t[0], position[1]-t[1], 0.-t[2] ]) for position in xy_ ]

#     # detector pixel is the escape direction in sample frame:
#     pixel_sampleF = [(quaternion.rotate_vectors(q_DS, pixel ) )   for pixel in xyz_]
    
       
#     return [position_i for position_i in pixel_sampleF]
    

In [5]:
xy = [np.array([3., 30.])]
xy_PC = np.array([x_PC, y_PC])

print ('this version', projOnSample(xy, alpha, xy_PC, L))

print ('Patrick', projOnSample_patrick(xy, alpha, xy_PC, L))

this version [array([-1.87402310e+03,  5.70000000e-01, -4.90484468e+03])]
Patrick [array([-1.87402310e+03,  5.70000000e-01, -4.90484468e+03])]


In [10]:
import plotly.io as pio
from IPython.display import Image

#continuous

file_discr = '../data/Al_BSE_mode:DS_tilt:70.0_Emin:15000.0_E0:20000.0_tolE:0.0001_tolW:1e-07.h5'

h5data_c = h5py.File(file_discr,'r+')
dir_cont = h5data_c['BSE']['block0_values'][1:4]

xyz_cont = np.array(zip(dir_cont[0], dir_cont[1], dir_cont[2])) 
xy_PC = np.array([x_PC*delta, y_PC*delta])

onDetector_cont = projOnDetector(list(xyz_cont), alpha, xy_PC, L)

trace_oD_1 = go.Scatter( x = [ xy[0]/delta for xy in onDetector_cont[0:20000]], y = [ xy[1]/delta for xy in onDetector_cont[0:20000]], mode = 'markers', marker=dict( size = 1, color = 'rgba(253, 192, 134, .6)',)
                       )

layout = go.Layout(
autosize=False,
width=640,
height=480,
#title = '10 keV incident electrons on a 70 degrees tilted Al sample',
font=dict( color='#7f7f7f'),
paper_bgcolor='rgba(0,0,0,0)',
plot_bgcolor='rgba(0,0,0,0)',
yaxis=dict(
gridcolor= '#7f7f7f',
title = 'y axis',
zerolinecolor='#dcdcdc',
range=[-240, 240]
),
xaxis=dict(
gridcolor= '#7f7f7f',
title = 'x axis',
zerolinecolor='#dcdcdc',
range=[-320, 320]
)
)
data = [trace_oD_1]
fig = go.Figure(data=data, layout=layout)
#py.iplot(fig, filename='on detector cont 15-30')


img_bytes = pio.to_image(fig, format='png', width=640, height=480, scale=2)
Image(img_bytes)

py.iplot(img_bytes)

#pio.write_image(fig, 'images/onDet_cont_15-30.png')



KeyError: "Unable to open object (object 'BSE' doesn't exist)"

In [12]:
# discrete
els_discr = pd.read_hdf('../data/Al_BSE_mode:DS_elastic:Ruth_vanilla_tilt:70.0_Emin:15000.0_E0:20000.0_tolE:0.0001_tolW:1e-07.h5', 'els')
len(els_discr)

197000

In [8]:
xyz_DS = els_discr[els_discr['outcome']=='bks'][['dx', 'dy', 'dz']].to_numpy()
xyz_DS.shape


(77851, 3)

In [13]:
xy_PC = np.array([x_PC*delta, y_PC*delta])

onDetector_DS = projOnDetector(list(xyz_DS), alpha, xy_PC, L)

trace_oD_2 = go.Scatter(
    x = [ xy[0]/delta for xy in onDetector_DS],
    y = [ xy[1]/delta for xy in onDetector_DS],
    mode = 'markers', 
    marker=dict(
             size = 2, 
             color = 'rgba(253, 192, 134, .6)',)
    
)

layout = go.Layout(
        #title = '10 keV incident electrons on a 70 degrees tilted Al sample',
        autosize=False,
        width=512,
        height=512,
        font=dict( color='#7f7f7f'),
        paper_bgcolor='rgba(0,0,0,0)',
        plot_bgcolor='rgba(0,0,0,0)',
        yaxis=dict(
             gridcolor= '#7f7f7f',
             title = 'y axis', 
             zerolinecolor='#dcdcdc', 
             range=[-128, 128]   
        ), 
        xaxis=dict(
             gridcolor= '#7f7f7f',
             title = 'x axis', 
             zerolinecolor='#dcdcdc', 
             range=[-128, 128]
        )
    )

data = [trace_oD_2]
fig = go.Figure(data=data, layout=layout)
fig.show()

In [91]:
fig = tools.make_subplots(rows=1, cols=2, subplot_titles=('15-30 keV', '25-30 keV'))

fig.append_trace(trace_oD_1, 1, 1)
fig.append_trace(trace_oD_2, 1, 2)

fig['layout'].update(title='CSDA',
                     height=480, 
                     width=1240,
                     font=dict( color='#7f7f7f'),
                     paper_bgcolor='rgba(0,0,0,0)',
                     plot_bgcolor='rgba(0,0,0,0)',
                     
                     xaxis1=dict(
                           gridcolor= '#7f7f7f',
                           title = 'x axis', 
                           zerolinecolor='#dcdcdc', 
                           range=[-320, 320]),
                     yaxis1=dict(
                           gridcolor= '#7f7f7f',
                           title = 'y axis', 
                           zerolinecolor='#dcdcdc', 
                           range=[-240, 240]),
                     
                     xaxis2=dict(
                           gridcolor= '#7f7f7f',
                           title = 'x axis', 
                           zerolinecolor='#dcdcdc', 
                           range=[-320, 320]), 
                     yaxis2=dict(
                           gridcolor= '#7f7f7f',
                           title = 'y axis', 
                           zerolinecolor='#dcdcdc', 
                           range=[-240, 240]),
                     
                     showlegend=False
             )
#py.iplot(fig, filename='cont 15-30 and 25-30')

This is the format of your plot grid:
[ (1,1) x1,y1 ]  [ (1,2) x2,y2 ]



Layout({
    'annotations': [{'font': {'size': 16},
                     'showarrow': False,
                     'text': '15-30 keV',
                     'x': 0.225,
                     'xanchor': 'center',
                     'xref': 'paper',
                     'y': 1.0,
                     'yanchor': 'bottom',
                     'yref': 'paper'},
                    {'font': {'size': 16},
                     'showarrow': False,
                     'text': '25-30 keV',
                     'x': 0.775,
                     'xanchor': 'center',
                     'xref': 'paper',
                     'y': 1.0,
                     'yanchor': 'bottom',
                     'yref': 'paper'}],
    'font': {'color': '#7f7f7f'},
    'height': 480,
    'paper_bgcolor': 'rgba(0,0,0,0)',
    'plot_bgcolor': 'rgba(0,0,0,0)',
    'showlegend': False,
    'title': {'text': 'CSDA'},
    'width': 1240,
    'xaxis': {'anchor': 'y',
              'domain': [0.0, 0.45],
              'grid

### distribution on detector at different energiers

In [106]:
energies_cont = h5data_c['BSE']['block0_values'][0]


trace_eD_cont = go.Scatter(
    x = energies_cont[0:20000],
    y = [ xy[1]/delta for xy in onDetector_cont[0:20000]],
    mode = 'markers', 
    marker=dict(
             size = 1, 
             color = 'rgba(253, 192, 134, .6)',)
    
)



data = [trace_eD_cont]
layout = go.Layout(
         #title = '10 keV incident electrons on a 70 degrees tilted Al sample',
         autosize=False,
         width=640,
         height=480,
         font=dict( color='#7f7f7f'),
         paper_bgcolor='rgba(0,0,0,0)',
         plot_bgcolor='rgba(0,0,0,0)',
         yaxis=dict(
              gridcolor= '#7f7f7f',
              title = 'y axis (pixels)', 
              zerolinecolor='#dcdcdc', 
              range=[-240, 240]   
         ), 
         xaxis=dict(
              gridcolor= '#7f7f7f',
              title = 'exit energy (eV)', 
              zerolinecolor='#dcdcdc', 
              range=[25000, 30000]
         )
     )
fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='energy distribution along y cont 25-30')

In [107]:
energies_DS = h5data_d['BSE']['block0_values'][0]


trace_eD_DS = go.Scatter(
    x = energies_DS[0:20000],
    y = [ xy[1]/delta for xy in onDetector_DS[0:20000]],
    mode = 'markers', 
    marker=dict(
             size = 1, 
             color = 'rgba(253, 192, 134, .6)',)
    
)



data = [trace_eD_DS]
fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='energy distribution along y DS 25-30')

In [111]:
import scipy.stats as st      
from scipy import interpolate

def kde_scipy( vals1, vals2, (a,b), (c,d), N, bw ):
    x = np.linspace(a,b,N)
    y = np.linspace(c,d,N)
    X,Y = np.meshgrid(x,y)
    positions = np.vstack([Y.ravel(), X.ravel()])

    values = np.vstack([vals1, vals2])
    kernel = st.gaussian_kde(values, bw_method = bw)
    Z = np.reshape(kernel(positions).T, X.shape)

    return [x, y, Z]


def make_kdetrace(varX, varY, (a,b), (c,d), N, bw, colorsc):
    x, y, Z = kde_scipy(varY, varX, (a,b), (c,d), N, bw )

    trace = go.Contour(
           z=Z,
           x=x,
           y=y,
           colorscale=colorsc,
           #reversescale=True,
           opacity=0.9,
           ncontours=20,
           contours=dict(
                coloring='fill', 
                showlines=False, 
                #start=0.001, 
                #end = 0.5
           ), 
            line=dict(
                width=0.5, 
                   ), 
            #zauto=False,
            #zmax=0.5
           
       )

    
    return trace


def make_kdePercLines(varX, varY, (a,b), (c,d), N, bw, colorsc):
    
    x, y, Z = kde_scipy(varY, varX, (a,b), (c,d), N, bw )

    # show percentage contours
    Zp = Z / Z.sum()
    
    n = 100
    t = np.linspace(0, Zp.max(), n)
    integral = ((Zp >= t[:, None, None]) * Zp).sum(axis=(1,2))

    f = interpolate.interp1d(integral, t)
    t_contours = f(np.array([0.9, 0.8, 0.7, 0.6, 0.5, 0.4])) # t_contours are the margins of an area containing a percentage of the points

    traces = dict()
    for index, t in enumerate(t_contours):
        # one percentage contour at a time
        traces[str(index)] = go.Contour(
                   x=x,
                   y=y,
                   z=Zp,
                   opacity=0.5,
                   showlegend=False,
                   autocontour=False,
                   autocolorscale=False,
                   colorscale=colorsc,
                   ncontours=1,
                   contours=dict(
                       coloring='lines',
                       
                       start=t_contours[index], 
                       end = t_contours[index]+1
                   ),
                   line=dict(
                        width=2.5, 
                   ), 
                   showscale=False
               )


    return traces

purples=[[0.0,   '#fcf9f7'],
 [0.1666666666666666, '#edcfc9'],
 [0.3333333333333333, '#daa2ac'],
 [0.5,                '#bc7897'],
 [0.6666666666666666, '#925684'],
 [0.8333333333333333, '#5f3868'],
 [1.0,                '#2d1e3e']]

In [112]:
x1, x2 = (25, 30)  # energy range
y1, y2 = (-240, 240) # pixels range

N = 400  # points to sample on a mesh for the KDE
bw = 0.01 # bandwidth

KDEtrace = make_kdetrace(energies_cont[0:40000]*0.001, 
                         [xy[1]/delta for xy in onDetector_cont[0:40000]], 
                         (x1, x2), (y1, y2), N, bw, purples)
data = [ KDEtrace]
figureKDE = go.Figure(data=data)

py.iplot(figureKDE, filename='KDE energy versus y axis cont 25-30')

In [113]:
energies_DS = h5data_d['BSE']['block0_values'][0]

KDEtrace = make_kdetrace(energies_DS[0:40000]*0.001, 
                         [xy[1]/delta for xy in onDetector_cont[0:40000]], 
                         (x1, x2), (y1, y2), N, bw, purples)
data = [ KDEtrace]
figureKDE = go.Figure(data=data)

py.iplot(figureKDE, filename='KDE energy versus y axis discrete 25-30')